In [2]:
!pip install transformers datasets torch faiss-cpu


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 21.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.5/27.5 MB 39.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 801.7 kB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 13.8 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [4]:
from datasets import load_dataset

dataset = load_dataset("Amod/mental_health_counseling_conversations")


In [17]:
import torch
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, Trainer, TrainingArguments
from datasets import load_dataset
# Instead of using train_test_split, we'll use Dataset.train_test_split
#from sklearn.model_selection import train_test_split

# Load dataset
dataset = load_dataset("Amod/mental_health_counseling_conversations")

# Split the dataset using Dataset.train_test_split
train_data = dataset['train'].train_test_split(test_size=0.2, seed=42)['train']  # 80% train
val_data = dataset['train'].train_test_split(test_size=0.2, seed=42)['test']  # 20% validation


# Load FLAN-T5 Small model and tokenizer
model_name = "google/flan-t5-small"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)

# Preprocess the dataset
def preprocess_data(examples):
    # Tokenize the context and response as input-output pairs for the Seq2Seq model
    inputs = tokenizer(examples['Context'], padding="max_length", truncation=True, max_length=512)
    targets = tokenizer(examples['Response'], padding="max_length", truncation=True, max_length=128)
    inputs['labels'] = targets['input_ids']
    return inputs

# Apply preprocessing to the train and validation datasets
train_data = train_data.map(preprocess_data, batched=True)
val_data = val_data.map(preprocess_data, batched=True)

# Remove unnecessary columns (Context, Response) from the dataset after preprocessing


# Setup training arguments
training_args = TrainingArguments(
    output_dir='./results',
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    num_train_epochs=5,
    logging_dir='./logs',
    logging_steps=10,
    save_strategy="epoch",  # Changed save_strategy to 'epoch' to match evaluation_strategy
    save_steps=500,
    save_total_limit=2,
    load_best_model_at_end=True,
    metric_for_best_model='loss',
)

# Initialize Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=val_data,
    tokenizer=tokenizer,
)

# Train the model
trainer.train()

# Save the fine-tuned model
trainer.save_model("fine_tuned_flan_t5")

# Now the model is fine-tuned and saved, we can use it for RAG

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


There were missing keys in the checkpoint model loaded: ['encoder.embed_tokens.weight', 'decoder.embed_tokens.weight'].


In [25]:
trainer.evaluate(train_data)

{'eval_loss': 2.8036255836486816,
 'eval_runtime': 65.2915,
 'eval_samples_per_second': 43.022,
 'eval_steps_per_second': 21.519,
 'epoch': 5.0}

In [26]:
trainer.evaluate(val_data)

{'eval_loss': 2.9024901390075684,
 'eval_runtime': 23.9355,
 'eval_samples_per_second': 29.371,
 'eval_steps_per_second': 14.706,
 'epoch': 5.0}

In [34]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

# Load the fine-tuned FLAN-T5 model and tokenizer
model_name = "/content/results/checkpoint-5620"  # Replace with the path to your fine-tuned model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)

# Function to perform inference
def generate_response(input_text):
    # Encode the input text
    inputs = tokenizer(input_text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    # The model.generate function call should be indented inside the generate_response function
    output_ids = model.generate(
        inputs.input_ids,
        max_length=500,
        num_beams=4,
        temperature=0.7,
        top_p=0.9,
        top_k=50,
        do_sample=True,        # Sampling instead of beam search
        no_repeat_ngram_size=3, # Avoid repeating 3-grams
        length_penalty=1.0,    # Adjust this value based on your preference
        early_stopping=True
    )
    response = tokenizer.decode(output_ids[0], skip_special_tokens=True)
    return response



# Example input text
input_text = "I'm going through some things with my feelings and myself. I barely sleep and I do nothing but think about how I'm worthless and how I shouldn't be here. I've never tried or contemplated suicide. I've always wanted to fix my issues, but I never get around to it. How can I change my feeling of being worthless to everyone?"

# Perform inference
response = generate_response(input_text)
print("Response from the model:", response)

Response from the model: I'm sorry to hear that you haven't tried or contemplated suicide. It sounds like you've been able to change your feeling of being worthless to everyone. It's a good idea to have a conversation with a mental health professional to discuss your feelings. If you're not sure what you want to do, you may want to talk to a psychiatrist about what you'd like to do. You may also want to ask a therapist if you are willing to help you with your feelings of worthlessness.
